In [1]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2018 NVIDIA Corporation
Built on Sat_Aug_25_21:08:04_Central_Daylight_Time_2018
Cuda compilation tools, release 10.0, V10.0.130


In [ ]:
#!pip install --user cupy-cuda100

In [2]:
import cupy
cupy.show_config()

CuPy Version          : 7.5.0
CUDA Root             : C:\Program Files\NVIDIA GPU Computing Toolkit\CUDA\v10.0
CUDA Build Version    : 10000
CUDA Driver Version   : 10010
CUDA Runtime Version  : 10000
cuBLAS Version        : 10000
cuFFT Version         : 10000
cuRAND Version        : 10000
cuSOLVER Version      : (10, 0, 0)
cuSPARSE Version      : 10000
NVRTC Version         : (10, 0)
cuDNN Build Version   : 7402
cuDNN Version         : 7402
NCCL Build Version    : None
NCCL Runtime Version  : None
CUB Version           : None
cuTENSOR Version      : None


In [ ]:
#!pip install --user --upgrade spacy[cuda100]

In [3]:
import spacy
import sys
from collections import defaultdict

spacy.require_gpu()

True

In [4]:
nlp = spacy.load('en_core_web_md')

In [5]:
chat_text = ('Hi my name is Donald Duck, I am American, and my bank account 32345128 with sort code 12-15-18. \
                My VISA is 4444333322221111 how do I get access to online banking? \
                I think I have $325 on my account when I checked on 10-05-2011 \
                I have 2 accounts with you. \
                My uncles sort is 090971 with account 12345678. \
                You can reach me on phone 01234 000 001 or donaldduck@gmail.com. \
                Ohh and my address is 1313 Webfoot Walk, Duckburg, Calisota')
chat_test_doc = nlp(chat_text)
ner = nlp.get_pipe('ner')
print(ner.predict(chat_test_doc))
print(type(ner))
for ent in chat_test_doc.ents:
    print(ent.text, ent.start_char, ent.end_char, ent.label_, spacy.explain(ent.label_))

<class 'spacy.pipeline.pipes.EntityRecognizer'>
Donald Duck 14 25 PERSON People, including fictional
American 32 40 NORP Nationalities or religious or political groups
32345128 62 70 CARDINAL Numerals that do not fall under another type
12 86 88 CARDINAL Numerals that do not fall under another type
VISA 115 119 ORG Companies, agencies, institutions, etc.
4444333322221111 123 139 DATE Absolute or relative dates or periods
325 211 214 MONEY Monetary values, including unit
10-05-2011 247 257 DATE Absolute or relative dates or periods
2 281 282 CARDINAL Numerals that do not fall under another type
090971 336 342 CARDINAL Numerals that do not fall under another type
01234 000 408 417 CARDINAL Numerals that do not fall under another type
Webfoot Walk 490 502 FAC Buildings, airports, highways, bridges, etc.
Duckburg 504 512 GPE Countries, cities, states
Calisota 514 522 GPE Countries, cities, states


In [54]:
from spacy import displacy

displacy.serve(chat_test_doc, style='ent')

E:\Anaconda\envs\ML-NLP-GPU\lib\runpy.py:193: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  "__main__", mod_spec)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [ ]:
#nlp = spacy.load('en')
text = u'Will Japan join the European Union? If yes, we should move to United States. Fasten your belts, America we are coming'


with nlp.disable_pipes('ner'):
    doc = nlp(chat_text)

threshold = 0.2
beams = nlp.entity.beam_parse([ doc ], beam_width = 16, beam_density = 0.0001)

entity_scores = defaultdict(float)
for beam in beams:
    for score, ents in nlp.entity.moves.get_beam_parses(beam):
        #print ('ents: {}, Score: {}'.format(ents, score))
        for start, end, label in ents:
            entity_scores[(start, end, label)] += score

print ('Entities and scores (detected with beam search)')
for key in entity_scores:
    start, end, label = key
    score = entity_scores[key]
    if ( score > threshold):
        print ('Label: {}, Text: {}, Score: {}'.format(label, doc[start:end], score))

### Let's create a Custom Named Entity 

#### Capture Email, Phone, Bank Account and Sort Code

In [6]:
data1 = 'My bank account is 09876543 with sort code 11-01-45.'
    
data3 = 'Bank Account 09780909, Sort Code 12-34-56'

data5 = 'Hi bank people. Need help with my account, account is 45674567, call me on 01345 567567'

data6 = 'Can you help me with my sort 34-23-12 and contact me using xyz@googlemail.dk'

data7 = 'I live here in the UK and need help with accessing my account. Bank acc is 09876543, 13-20-54. Let me know on 1290 344 456 or helpme@outlook.com'

data8 = 'Sort Code 33-34-35, Bank Account 33445566'

data10 = 'Help, my sort code is 22-23-71, contact me using Daisy@googlemail.co.uk, ohh account no is 44435987'


In [7]:
TRAIN_DATA = [
    (data1, {
        'entities': [(19, 27, 'BANK_ACCOUNT'), (43, 51, 'SORT_CODE')]
    }),
     (data3, {
         'entities': [(13, 21, 'BANK_ACCOUNT'), (33, 41, 'SORT_CODE')]
    }),
     (data5, {
         'entities': [(54, 62, 'BANK_ACCOUNT'), (75, 87, 'PHONE')]
    }),
     (data6, {
         'entities': [(29, 37, 'SORT_CODE'), (59, 76, 'EMAIL')]
    }),
     (data7, {
         'entities': [(75, 83, 'BANK_ACCOUNT'), (85, 93, 'SORT_CODE'), (110, 122, 'PHONE'), (126, 144, 'EMAIL')]
    }),
     (data8, {
         'entities': [(10, 18, 'SORT_CODE'), (33, 41, 'BANK_ACCOUNT')]
    }),
     (data10, {
         'entities': [(22, 30, 'SORT_CODE'), (49, 71, 'EMAIL'), (91, 99, 'BANK_ACCOUNT')]
    }),

]

In [8]:
TRAIN_DATA_1 = [
    ('My sort is 123456', {
        'entities': [(11, 17, 'SORT_CODE')]
    }), 
    ('My name is John Larsen and I live at 4 Hull Way, St Neots, Cambs, PE196GS', {
        'entities': [(11, 22, 'PERSON'), (37, 73, 'ADDRESS')]
    }), 
    ('Hi Oliver here. I need help with my account 12345555, sort 934523', {
        'entities': [(44, 52, 'BANK_ACCOUNT'), (59, 65, 'SORT_CODE'), (3, 9, 'PERSON')]
    }), 
    ('Sort code: 09-23-14', {
        'entities': [(11, 19, 'SORT_CODE')]
    }), 
    ('Ben here. I need help with account 87875656, sort code 03-12-34', {
        'entities': [(35, 43, 'BANK_ACCOUNT'), (55, 63, 'SORT_CODE')]
    }), 
    ('To day on 21-05-2020 I, Boris Jonson, need help with credit card 01234333322223456', {
        'entities': [(10, 20, 'DATE'), (24, 36, 'PERSON'), (65, 81, 'BANK_CARD')]
    }), 
    ('My name is Bruce Wayne and I have a question about my sort code 871234', {
        'entities': [(11, 22, 'PERSON'), (64, 70, 'SORT_CODE')]
    }), 
    ('Need help, Live at 15 Old Bourne Way in Stevenage, SG135AD', {
        'entities': [(19, 58, 'ADDRESS')]
    }), 
    ('I am Susan Harding I live in Manor Hours, Long Road, Knebworth, Herts', {
        'entities': [(5, 18, 'PERSON'), (29, 69, 'ADDRESS')]
    }), 
    ('Sort: 953423, account: 98761234, card: 1234432156788765', {
        'entities': [(6, 12, 'SORT_CODE'), (23, 31, 'BANK_ACCOUNT'), (39, 56, 'BANK_CARD')]
    }), 
    ('Alfredo Elliott, please help me with my card 7676 8989 1212 5656', {
        'entities': [(0, 15, 'PERSON'), (45, 64, 'BANK_CARD')]
    }), 
    ('You are speaking with Ahmad Hayden, need your guidance on sort code issue. My code is 123123', {
        'entities': [(22, 34, 'PERSON'), (86, 92, 'SORT_CODE')]
    }), 
    ('Hi I am Emanuel Velasquez. Can I please request you help with my address 234 No Road in Enfield, EN174OP', {
        'entities': [(8, 25, 'PERSON'), (65, 104, 'ADDRESS')]
    }), 
    ('My address is 123 Emerson Road - KIRDFORD - RH14 8FZ', {
        'entities': [(14, 52, 'ADDRESS')]
    }), 
    ('Hey my name is Mohamed Cameron and I live at 56 Crown Street, London, SW99 4UN', {
        'entities': [(15, 30, 'PERSON'), (45, 78, 'ADDRESS')]
    }), 
    ('I need you to help me on this date 25-05-20, regards Jenny', {
        'entities': [(35, 43, 'DATE'), (53, 59, 'PERSON')]
    }), 
    ('Please help me before this day 01/06/20. Kind regards Kristina Wilkerson', {
        'entities': [(31, 39, 'DATE'), (54, 72, 'PERSON')]
    }), 
    ('James Croydon Goodard reaching out, need access now account is 45454745, sort is 898973', {
        'entities': [(0, 21, 'PERSON'), (63, 71, 'BANK_ACCOUNT'), (81, 87, 'SORT_CODE')]
    })
]

In [9]:
import address_data_generator

address_entries = address_data_generator.create_entries(1000)
#print(address_entries)


In [10]:
import person_data_generator

person_entries = person_data_generator.create_entries(1000)
#print(person_entries)


In [11]:
import date_data_generator

date_entries = date_data_generator.create_entries(1000)
#print(date_entries)

In [12]:
import sortcode_data_generator

sortcode_entries = sortcode_data_generator.create_entries(2000)
#print(sortcode_entries)

In [13]:
TRAIN_DATA_2 = TRAIN_DATA + TRAIN_DATA_1 + address_entries + date_entries + person_entries + sortcode_entries
print(len(TRAIN_DATA_2))

5025


In [15]:
import random
from tqdm import tqdm

ner = nlp.get_pipe('ner')

DATA = TRAIN_DATA_2

n_iter=20
# add labels, Trains data based on annotations 
for _, annotations in DATA:
    for ent in annotations.get('entities'):
        print(ent[2])
        ner.add_label(ent[2])

# get names of other pipes to disable them during training
other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
with nlp.disable_pipes(*other_pipes):  # only train NER
    optimizer = nlp.begin_training()
    for itn in range(n_iter):
        random.shuffle(DATA)
        losses = {}
        for text, annotations in tqdm(DATA):
            nlp.update(
                [text],  # batch of texts
                [annotations],  # batch of annotations
                drop=0.5,  # dropout 
                sgd=optimizer,  # callable to update weights
                losses=losses)
        print(losses)

SORT_CODE
PERSON
DATE
SORT_CODE
ADDRESS
PERSON
DATE
PERSON
SORT_CODE
SORT_CODE
PERSON
PERSON
PERSON
PERSON
PERSON
DATE
DATE
ADDRESS
PERSON
PERSON
PERSON
DATE
PERSON
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
DATE
PERSON
SORT_CODE
DATE
PERSON
SORT_CODE
SORT_CODE
DATE
DATE
PERSON
PERSON
SORT_CODE
SORT_CODE
DATE
PERSON
PERSON
DATE
DATE
PERSON
ADDRESS
SORT_CODE
DATE
SORT_CODE
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
DATE
PERSON
DATE
SORT_CODE
DATE
ADDRESS
PERSON
ADDRESS
PERSON
PERSON
SORT_CODE
DATE
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
DATE
ADDRESS
DATE
PERSON
ADDRESS
DATE
DATE
SORT_CODE
PERSON
SORT_CODE
ADDRESS
PERSON
PERSON
DATE
ADDRESS
DATE
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
DATE
ADDRESS
DATE
DATE
PERSON
PERSON
SORT_CODE
PERSON
ADDRESS
ADDRESS
PERSON
PERSON
ADDRESS
SORT_CODE
DATE
ADDRESS
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
ADDRESS
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
DATE
SORT_CODE
ADDRESS
SORT_CODE
PERSON
SORT_CODE
P

SORT_CODE
PERSON
SORT_CODE
DATE
PERSON
DATE
DATE
DATE
PERSON
SORT_CODE
SORT_CODE
SORT_CODE
DATE
SORT_CODE
PERSON
PERSON
ADDRESS
DATE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
SORT_CODE
DATE
SORT_CODE
ADDRESS
ADDRESS
PERSON
SORT_CODE
SORT_CODE
DATE
SORT_CODE
PERSON
SORT_CODE
PERSON
DATE
SORT_CODE
SORT_CODE
SORT_CODE
DATE
DATE
PERSON
ADDRESS
PERSON
SORT_CODE
DATE
ADDRESS
DATE
SORT_CODE
PERSON
SORT_CODE
DATE
SORT_CODE
SORT_CODE
DATE
SORT_CODE
PERSON
DATE
PERSON
PERSON
PERSON
SORT_CODE
PERSON
PERSON
ADDRESS
SORT_CODE
SORT_CODE
PERSON
ADDRESS
ADDRESS
ADDRESS
ADDRESS
PERSON
DATE
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
PERSON
SORT_CODE
SORT_CODE
DATE
SORT_CODE
SORT_CODE
DATE
DATE
SORT_CODE
SORT_CODE
DATE
DATE
PERSON
SORT_CODE
SORT_CODE
ADDRESS
PERSON
PERSON
DATE
ADDRESS
PERSON
DATE
DATE
ADDRESS
PERSON
ADDRESS
ADDRESS
SORT_CODE
SORT_CODE
DATE
SORT_CODE
SORT_CODE
PERSON
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
PERSON
DATE
SORT_CODE
PERSON
DATE
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
DATE

DATE
ADDRESS
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
DATE
ADDRESS
SORT_CODE
PERSON
PERSON
DATE
DATE
PERSON
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
ADDRESS
PERSON
SORT_CODE
SORT_CODE
ADDRESS
ADDRESS
ADDRESS
ADDRESS
PERSON
PERSON
ADDRESS
SORT_CODE
SORT_CODE
SORT_CODE
PERSON
DATE
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
PERSON
PERSON
DATE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
DATE
DATE
DATE
ADDRESS
SORT_CODE
PERSON
DATE
ADDRESS
SORT_CODE
DATE
SORT_CODE
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
ADDRESS
SORT_CODE
PERSON
SORT_CODE
SORT_CODE
SORT_CODE
ADDRESS
DATE
SORT_CODE
SORT_CODE
ADDRESS
PERSON
PERSON
DATE
SORT_CODE
ADDRESS
PERSON
SORT_CODE
DATE
DATE
PERSON
ADDRESS
PERSON
DATE
SORT_CODE
ADDRESS
ADDRESS
PERSON
PERSON
PERSON
ADDRESS
PERSON
PERSON
SORT_CODE
PERSON
PERSON
DATE
DATE
SORT_CODE
DATE
ADDRESS
SORT_CODE
EMAIL

SORT_CODE
SORT_CODE
SORT_CODE
PERSON
PERSON
PERSON
SORT_CODE
ADDRESS
DATE
SORT_CODE
SORT_CODE
ADDRESS
DATE
SORT_CODE
DATE
SORT_CODE
PERSON
ADDRESS
PERSON
SORT_CODE
ADDRESS
SORT_CODE
PERSON
ADDRESS
SORT_CODE
SORT_CODE
PERSON
ADDRESS
DATE
ADDRESS
ADDRESS
PERSON
ADDRESS
SORT_CODE
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
ADDRESS
SORT_CODE
ADDRESS
ADDRESS
PERSON
PERSON
SORT_CODE
ADDRESS
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
SORT_CODE
DATE
ADDRESS
ADDRESS
SORT_CODE
DATE
DATE
DATE
PERSON
PERSON
PERSON
SORT_CODE
SORT_CODE
DATE
SORT_CODE
ADDRESS
SORT_CODE
DATE
SORT_CODE
SORT_CODE
PERSON
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
SORT_CODE
DATE
SORT_CODE
PERSON
ADDRESS
PERSON
BANK_CARD
SORT_CODE
SORT_CODE
PERSON
ADDRESS
DATE
PERSON
ADDRESS
ADDRESS
PERSON
SORT_CODE
SORT_CODE
ADDRESS
PERSON
SORT_CODE
DATE
DATE
ADDRESS
PERSON
DATE
DATE
SORT_CODE


  6%|▌         | 301/5025 [00:20<05:06, 15.39it/s]


...

 83%|████████▎ | 4168/5025 [05:06<00:59, 14.37it/s]


 89%|████████▉ | 4464/5025 [05:26<00:36, 15.45it/s]


 95%|█████████▍| 4760/5025 [05:47<00:18, 14.35it/s]


100%|██████████| 5025/5025 [06:06<00:00, 13.71it/s]

{'ner': 32865.861390345555}


In [ ]:
# internal test to check mappings of input test data, that is, string locations of entities
for text, _ in TRAIN_DATA_2:
    doc = nlp(text)
    print('Entities', [(ent.text, ent.label_) for ent in doc.ents])

In [57]:
new_chat_test_doc = nlp(chat_text)
#print(new_chat_test_doc)
displacy.render(new_chat_test_doc,style='ent',jupyter=True)
#displacy.serve(new_chat_test_doc, style='ent')

#### Finding the confidence score for an entity 

In [23]:
for ent in new_chat_test_doc.ents:
    print(ent.text, ent.start_char, ent.end_char, ent.label_, spacy.explain(ent.label_))

print()
print(len(TRAIN_DATA_2))

Donald Duck 14 25 PERSON People, including fictional
American 32 40 PERSON People, including fictional
12-15-18.                  86 112 SORT_CODE None
4444333322221111 123 139 SORT_CODE None
10-05-2011                  247 274 DATE Absolute or relative dates or periods
090971 336 342 SORT_CODE None
01234 000 001 408 421 ADDRESS None
1313 Webfoot Walk, Duckburg, Calisota 485 522 ADDRESS None

5025


In [24]:
threshold = 0.2
beams = nlp.entity.beam_parse([new_chat_test_doc], beam_width = 16, beam_density = 0.0001)

entity_scores = defaultdict(float)
for beam in beams:
    for score, ents in nlp.entity.moves.get_beam_parses(beam):
        #print ('ents: {}, Score: {}'.format(ents, score))
        for start, end, label in ents:
            entity_scores[(start, end, label)] += score

print ('Entities and scores (detected with beam search)')
for key in entity_scores:
    start, end, label = key
    score = entity_scores[key]
    if ( score > threshold):
        print ('Label: {}, Text: {}, Score: {}'.format(label, new_chat_test_doc[start:end], score))

Entities and scores (detected with beam search)
Label: PERSON, Text: Donald Duck, Score: 1.0000000000000002
Label: PERSON, Text: American, Score: 1.0000000000000002
Label: SORT_CODE, Text: 12-15-18.                 , Score: 1.0000000000000002
Label: SORT_CODE, Text: 4444333322221111, Score: 1.0000000000000002
Label: DATE, Text: 10-05-2011                 , Score: 1.0000000000000002
Label: SORT_CODE, Text: 2, Score: 0.7383292153453194
Label: SORT_CODE, Text: 090971, Score: 1.0000000000000002
Label: ADDRESS, Text: 01234 000 001, Score: 1.0000000000000002
Label: SORT_CODE, Text: donaldduck@gmail.com, Score: 0.29453676202147744
Label: ADDRESS, Text: 1313 Webfoot Walk, Duckburg, Calisota, Score: 1.0000000000000002


### Executing the test suit

In [106]:
from itertools import groupby

def split_str_to_words(string):
    x = string.replace(",", " ")
    x = x.replace(";", " ")
    x = x.replace(":", " ")
    return x.split()

# Replace a token with "REDACTED" if it is a name
def replace_name_with_placeholder(token):
    if token.ent_iob != 0 and token.ent_type_ == "PERSON":
        return "PERSON "
    elif token.ent_iob != 0 and token.ent_type_ == "ADDRESS":
        return "ADDRESS "
    elif token.ent_iob != 0 and token.ent_type_ == "SORT_CODE":
        return "SORT_CODE "
    elif token.ent_iob != 0 and token.ent_type_ == "DATE":
        return "DATE "
    else:
        return token.string

def remove_dupe_entities(tokens):
    results = [w[0] for w in groupby(tokens)]
    return results

def redact_it(sentence):
    print("INPUT: " + sentence)
    doc = nlp(sentence)
#    for ent in doc.ents:
#        print(ent.text + ' *** ' + ent.label_)
#        ent.merge() ### Can't get this current installation to work throws an exception index error cupy
    tokens = map(replace_name_with_placeholder, doc)
    #print("Tokens:" + str(list(tokens)))
    tokens = remove_dupe_entities(tokens)
    redacted_sentence = "".join(tokens)
    print("OUTPUT: " + redacted_sentence)
    return redacted_sentence
    
def redact_and_score(input, expected_output):
    
    redacted_input = redact_it(input)
    
    full_match = redacted_input == expected_output

    redacted_input_list = split_str_to_words(redacted_input)
    #print("Predicted redacted sentence list:" + str(redacted_input_list))
    expected_output_list = split_str_to_words(expected_output)

    # let's find out how many entities we predicted
    #print("Person redaction sentence count: " + str(redacted_input_list.count('PERSON')))
    person_labels = (redacted_input_list.count('PERSON'), expected_output_list.count('PERSON'))
    address_labels = (redacted_input_list.count('ADDRESS'), expected_output_list.count('ADDRESS'))
    sortcode_labels = (redacted_input_list.count('SORT_CODE'), expected_output_list.count('SORT_CODE'))
    date_labels = (redacted_input_list.count('DATE'), expected_output_list.count('DATE'))

    # returns: Full match: True/False, Person: (x, y). Location: (x, y), Sortcode: (x, y), Date: (x, y)   ---> Here x is predicted and y is the truth
    return full_match, {'PERSON': person_labels}, {'ADDRESS': address_labels}, {'SORT_CODE': sortcode_labels}, {'DATE': date_labels}

In [107]:
import pandas as pd

df = pd.read_excel (r'PII Redaction.xls')

#print(df.iloc[0:,[1,2]])
#print(df[df.columns[[1,2]]])
#print(df[df.columns[1]])
#print(df[df.columns[2]])

#results = [redact_and_score_detailed(input, expected_output) for input, expected_output in zip(df[' Utterance'], df['Expected Redacted Output'])]
results = [redact_and_score(input, expected_output) for input, expected_output in zip(df[' Utterance'], df['Expected Redacted Output'])]

for entry in results:
    print(entry)

INPUT: My name is Roger and I live in London
OUTPUT: My name is PERSON and I live in PERSON 
INPUT: Hey! Ben here
OUTPUT: Hey! PERSON here
INPUT: Hi,I am Andrew and need help with my pin enquiry.
OUTPUT: Hi,I am PERSON and need help with my pin enquiry.
INPUT: Hey Bot,I am Mr.Right
OUTPUT: Hey Bot,I am PERSON .Right
INPUT: I,Jackson Watts would like to open an account in Barclays
OUTPUT: I,PERSON would like to open an account in Barclays
INPUT: Robie William here,Hi
OUTPUT: PERSON here,Hi
INPUT: I am Sultan,how can you help me with my account?
OUTPUT: I am PERSON ,how can you help me with my account?
INPUT: Can you guide me to unlock my account?My name is Rose Mary but you can call me Rose.
OUTPUT: Can you guide me to unlock my account?My name is PERSON but you can call me Rose.
INPUT: My mum(Joan Haynes) has an saving account in Barclays and she would like to withdraw her money and close the account
OUTPUT: My ADDRESS 
INPUT: One of my relatives moved back home and asked me to check d

OUTPUT: I prefer mails to DATE than to posts
INPUT: I am having issues accessing my online account registered using my mail id abc.def@mail.org.Is it because I am using public IP address 2a10:c9f:381f:5410:0:5ge3:7fu3:9b7e ?
OUTPUT: I am having issues accessing my online account registered using my mail id abc.def@mail.org.Is it because I am using public IP address SORT_CODE :c9f:381f:5410:0:5ge3:7fu3:9b7e ?
INPUT: abc.def@mail.com
OUTPUT: abc.def@mail.com
INPUT: I changed my ip from 129.129.76.215 to 77.123.456.789
OUTPUT: I changed my ip from DATE to 77.123.456.789
INPUT: My mobile ip is 12.156.234.43 on which I am having issues to install app
OUTPUT: My mobile ip is SORT_CODE on which I am having issues to install app
INPUT: IP address of my device is 234.678.98.123
OUTPUT: IP address of my device is SORT_CODE 
INPUT: my mac book's address is 10.0.0.0
OUTPUT: my mac book's address is SORT_CODE 
INPUT: Hey! I am on holiday to Thailand, trying to access my account on my laptop having 